In [5]:
# Data Pre-Processing

In [6]:
import csv
import mysql.connector
import zipfile
import os

conn = mysql.connector.connect(
    host="localhost",
    user="monty",
    password="sushiSQL",
    database="HealthCareAnalytics"
)
cursor = conn.cursor()


## Creating the Queries

In [7]:
create_table_queries = {
    "CDC_Chronic_Disease_Indicators": """
    CREATE TABLE IF NOT EXISTS `CDC_Chronic_Disease_Indicators` (
        `YearStart` INT,
        `YearEnd` INT,
        `LocationAbbr` VARCHAR(50),
        `LocationDesc` VARCHAR(100),
        `DataSource` VARCHAR(100),
        `Topic` VARCHAR(100),
        `Question` VARCHAR(500),
        `Response` VARCHAR(500),
        `DataValueUnit` VARCHAR(50),
        `DataValueType` VARCHAR(50),
        `DataValue` VARCHAR(50),
        `DataValueAlt` VARCHAR(50),
        `DataValueFootnoteSymbol` VARCHAR(50),
        `DatavalueFootnote` VARCHAR(500),
        `LowConfidenceLimit` FLOAT,
        `HighConfidenceLimit` FLOAT,
        `StratificationCategory1` VARCHAR(100),
        `Stratification1` VARCHAR(100),
        `StratificationCategory2` VARCHAR(100),
        `Stratification2` VARCHAR(100),
        `StratificationCategory3` VARCHAR(100),
        `Stratification3` VARCHAR(100),
        `GeoLocation` VARCHAR(100),
        `ResponseID` INT,
        `LocationID` INT,
        `TopicID` INT,
        `QuestionID` INT,
        `DataValueTypeID` INT,
        `StratificationCategoryID1` INT,
        `StratificationID1` INT,
        `StratificationCategoryID2` INT,
        `StratificationID2` INT,
        `StratificationCategoryID3` INT,
        `StratificationID3` INT,
        PRIMARY KEY (`YearStart`)
    )
    """,

    "CDC_HS_Cigar_Use": """
    CREATE TABLE IF NOT EXISTS `CDC_HS_Cigar_Use` (
        `YEAR` INT,
        `LocationAbbr` VARCHAR(50),
        `LocationDesc` VARCHAR(100),
        `DataSource` VARCHAR(100),
        `Topic` VARCHAR(100),
        `Subtopic` VARCHAR(100),
        `ShortQuestionText` VARCHAR(500),
        `Greater_Risk_Question` VARCHAR(500),
        `Description` VARCHAR(500),
        `Data_Value_Symbol` VARCHAR(50),
        `Data_Value_Type` VARCHAR(50),
        `Greater_Risk_Data_Value` FLOAT,
        `Greater_Risk_Data_Value_Footnote_Symbol` VARCHAR(50),
        `Greater_Risk_Data_Value_Footnote` VARCHAR(500),
        `Greater_Risk_Low_Confidence_Limit` FLOAT,
        `Greater_Risk_High_Confidence_Limit` FLOAT,
        `Lesser_Risk_Question` VARCHAR(500),
        `Lesser_Risk_Data_Value` FLOAT,
        `Lesser_Risk_Data_Value_Footnote_Symbol` VARCHAR(50),
        `Lesser_Risk_Data_Value_Footnote` VARCHAR(500),
        `Lesser_Risk_Low_Confidence_Limit` FLOAT,
        `Lesser_Risk_High_Confidence_Limit` FLOAT,
        `Sample_Size` INT,
        `Sex` VARCHAR(50),
        `Race` VARCHAR(50),
        `Grade` VARCHAR(50),
        `SexualIdentity` VARCHAR(50),
        `SexOfSexualContacts` VARCHAR(50),
        `GeoLocation` VARCHAR(100),
        `TopicId` INT,
        `SubTopicID` INT,
        `QuestionCode` VARCHAR(50),
        `LocationId` INT,
        `StratID1` INT,
        `StratID2` INT,
        `StratID3` INT,
        `StratID4` INT,
        `StratID5` INT,
        `StratificationType` VARCHAR(50),
        `StratID6` INT,
        PRIMARY KEY (`YEAR`)
    )
    """,

    "CMS_Specific_Chronic_Conditions": """
    CREATE TABLE IF NOT EXISTS `CMS_Specific_Chronic_Conditions` (
        `Bene_Geo_Lvl` INT,
        `Bene_Geo_Desc` VARCHAR(100),
        `Bene_Geo_Cd` VARCHAR(50),
        `Bene_Age_Lvl` VARCHAR(50),
        `Bene_Demo_Lvl` VARCHAR(50),
        `Bene_Demo_Desc` VARCHAR(100),
        `Bene_Cond` VARCHAR(100),
        `Prvlnc` VARCHAR(100),
        `Tot_Mdcr_Stdzd_Pymt_PC` FLOAT,
        `Tot_Mdcr_Pymt_PC` FLOAT,
        `Hosp_Readmsn_Rate` FLOAT,
        `ER_Visits_Per_1000_Benes` FLOAT,
        PRIMARY KEY (`Bene_Geo_Lvl`)
    )
    """,

    "CVD_cleaned": """
    CREATE TABLE IF NOT EXISTS `CVD_cleaned` (
        `General_Health` VARCHAR(100),
        `Checkup` VARCHAR(100),
        `Exercise` VARCHAR(100),
        `Heart_Disease` VARCHAR(100),
        `Skin_Cancer` VARCHAR(100),
        `Other_Cancer` VARCHAR(100),
        `Depression` VARCHAR(100),
        `Diabetes` VARCHAR(100),
        `Arthritis` VARCHAR(100),
        `Sex` VARCHAR(50),
        `Age_Category` VARCHAR(50),
        `Height_cm` FLOAT,
        `Weight_kg` FLOAT,
        `BMI` FLOAT,
        `Smoking_History` VARCHAR(100),
        `Alcohol_Consumption` VARCHAR(100),
        `Fruit_Consumption` VARCHAR(100),
        `Green_Vegetables_Consumption` VARCHAR(100),
        `FriedPotato_Consumption` VARCHAR(100),
        PRIMARY KEY (`General_Health`)
    )
    """,

    "Kaggle_HeartAttack_Prediction_heart": """
    CREATE TABLE IF NOT EXISTS `Kaggle_HeartAttack_Prediction_heart` (
        `age` INT,
        `sex` VARCHAR(50),
        `cp` INT,
        `trtbps` INT,
        `chol` INT,
        `fbs` INT,
        `restecg` INT,
        `thalachh` INT,
        `exng` INT,
        `oldpeak` FLOAT,
        `slp` INT,
        `caa` INT,
        `thall` INT,
        `output` INT,
        PRIMARY KEY (`age`)
    )
    """,

    "Kaggle_HeartAttack_Prediction_o2Saturation": """
    CREATE TABLE IF NOT EXISTS `Kaggle_HeartAttack_Prediction_o2Saturation` (
        `o2Saturation` FLOAT,
        PRIMARY KEY (`o2Saturation`)
    )
    """,

    "Heart_Disease_Prediction": """
    CREATE TABLE IF NOT EXISTS `Heart_Disease_Prediction` (
        `Age` INT,
        `Sex` VARCHAR(50),
        `Chest_pain_type` INT,
        `BP` INT,
        `Cholesterol` INT,
        `FBS_over_120` INT,
        `EKG_results` INT,
        `Max_HR` INT,
        `Exercise_angina` INT,
        `ST_depression` FLOAT,
        `Slope_of_ST` INT,
        `Number_of_vessels_fluro` INT,
        `Thallium` INT,
        `Heart_Disease` INT,
        PRIMARY KEY (`Age`)
    )
    """,

    "heart_failure_clinical_records_dataset": """
    CREATE TABLE IF NOT EXISTS `heart_failure_clinical_records_dataset` (
        `age` INT,
        `anaemia` INT,
        `creatinine_phosphokinase` INT,
        `diabetes` INT,
        `ejection_fraction` INT,
        `high_blood_pressure` INT,
        `platelets` FLOAT,
        `serum_creatinine` FLOAT,
        `serum_sodium` INT,
        `sex` INT,
        `smoking` INT,
        `time` INT,
        `DEATH_EVENT` INT,
        PRIMARY KEY (`age`)
    )
    """,

    "Kaggle_Indicators_of_HeartDesease_heart_2020_cleaned": """
    CREATE TABLE IF NOT EXISTS `Kaggle_Indicators_of_HeartDesease_heart_2020_cleaned` (
        `HeartDisease` INT,
        `BMI` FLOAT,
        `Smoking` INT,
        `AlcoholDrinking` INT,
        `Stroke` INT,
        `PhysicalHealth` INT,
        `MentalHealth` INT,
        `DiffWalking` INT,
        `Sex` VARCHAR(50),
        `AgeCategory` VARCHAR(50),
        `Race` VARCHAR(50),
        `Diabetic` INT,
        `PhysicalActivity` INT,
        `GenHealth` INT,
        `SleepTime` INT,
        `Asthma` INT,
        `KidneyDisease` INT,
        `SkinCancer` INT,
        PRIMARY KEY (`HeartDisease`)
    )
    """,

    "Kaggle_Indicators_of_HeartDesease_heart_2022_with_nans": """
    CREATE TABLE IF NOT EXISTS `Kaggle_Indicators_of_HeartDesease_heart_2022_with_nans` (
        `State` VARCHAR(100),
        `Sex` VARCHAR(50),
        `GeneralHealth` INT,
        `PhysicalHealthDays` INT,
        `MentalHealthDays` INT,
        `LastCheckupTime` INT,
        `PhysicalActivities` INT,
        `SleepHours` INT,
        `RemovedTeeth` INT,
        `HadHeartAttack` INT,
        `HadAngina` INT,
        `HadStroke` INT,
        `HadAsthma` INT,
        `HadSkinCancer` INT,
        `HadCOPD` INT,
        `HadDepressiveDisorder` INT,
        `HadKidneyDisease` INT,
        `HadArthritis` INT,
        `HadDiabetes` INT,
        `DeafOrHardOfHearing` INT,
        `BlindOrVisionDifficulty` INT,
        `DifficultyConcentrating` INT,
        `DifficultyWalking` INT,
        `DifficultyDressingBathing` INT,
        `DifficultyErrands` INT,
        `SmokerStatus` INT,
        `ECigaretteUsage` INT,
        `ChestScan` INT,
        `RaceEthnicityCategory` VARCHAR(50),
        `AgeCategory` VARCHAR(50),
        `HeightInMeters` FLOAT,
        `WeightInKilograms` FLOAT,
        `BMI` FLOAT,
        `AlcoholDrinkers` INT,
        `HIVTesting` INT,
        `FluVaxLast12` INT,
        `PneumoVaxEver` INT,
        `TetanusLast10Tdap` INT,
        `HighRiskLastYear` INT,
        `CovidPos` INT,
        PRIMARY KEY (`State`)
    )
    """,
}



## Adding the data

In [8]:
import chardet

# Execute the create table queries
for table_name, create_table_query in create_table_queries.items():
    cursor.execute(create_table_query)
    print(f"Table '{table_name}' created successfully!")

files = {
    "CDC_Chronic_Disease_Indicators": "../data/original_data/CDC_Chronic_Disease_Indicators.csv",
    "CDC_HS_Cigar_Use": "../data/original_data/CDC_HS_Cigar_Use.csv",
    "CMS_Specific_Chronic_Conditions": "../data/original_data/CMS_Specific_Chronic_Conditions.csv",
    "CVD_cleaned": "../data/original_data/CVD_cleaned.csv",
    "heart": "../data/original_data/heart.csv",
    "o2Saturation": "../data/original_data/o2Saturation.csv",
    "Heart_Disease_Prediction": "../data/original_data/Heart_Disease_prediction.csv",
    "heart_2020_cleaned": "../data/original_data/heart_2020_cleaned.csv",
    "heart_2022_with_nans": "../data/original_data/heart_2022_with_nans.csv",
}

# Execute the create table queries
for table_name, create_table_query in create_table_queries.items():
    cursor.execute(create_table_query)
    print(f"Table '{table_name}' created successfully!")

# Function to insert data from CSV into MySQL without duplicates
def insert_data_from_csv(table_name, csv_path):
    with open(csv_path, 'r') as csv_file:
        csv_reader = csv.DictReader(csv_file)
        for row in csv_reader:
            # Handle empty or invalid ResponseID values
            if not row['ResponseID']:
                row['ResponseID'] = None  # Replace empty value with NULL

            # Validate and clean other data as needed

            # Prepare the column names and placeholders for the SQL INSERT statement
            columns = ', '.join(row.keys())
            placeholders = ', '.join(['%s'] * len(row))

            # Once data is validated and cleaned, proceed with insertion
            try:
                query = f"INSERT INTO `{table_name}` ({columns}) VALUES ({placeholders})"
                cursor.execute(query, tuple(row.values()))
                conn.commit()
            except Exception as e:
                print(f"Error inserting data into table {table_name}: {e}")

# Function to get the primary key column based on table name and header
def get_primary_key_column(table_name, header):
    # Return the first column of the header as the primary key column
    if len(header) > 0:
        return header[0]
    else:
        print(f"No columns found in the header for table {table_name}. Skipping insertion.")
        return None

# Loop through each CSV file and insert data into the corresponding table
for table_name, csv_path in files.items():
    print(f"Inserting data from {table_name} into MySQL")
    insert_data_from_csv(table_name, csv_path)

# Close MySQL connection
cursor.close()
conn.close()

Table 'CDC_Chronic_Disease_Indicators' created successfully!
Table 'CDC_HS_Cigar_Use' created successfully!
Table 'CMS_Specific_Chronic_Conditions' created successfully!
Table 'CVD_cleaned' created successfully!
Table 'Kaggle_HeartAttack_Prediction_heart' created successfully!
Table 'Kaggle_HeartAttack_Prediction_o2Saturation' created successfully!
Table 'Heart_Disease_Prediction' created successfully!
Table 'heart_failure_clinical_records_dataset' created successfully!
Table 'Kaggle_Indicators_of_HeartDesease_heart_2020_cleaned' created successfully!
Table 'Kaggle_Indicators_of_HeartDesease_heart_2022_with_nans' created successfully!
Table 'CDC_Chronic_Disease_Indicators' created successfully!
Table 'CDC_HS_Cigar_Use' created successfully!
Table 'CMS_Specific_Chronic_Conditions' created successfully!
Table 'CVD_cleaned' created successfully!
Table 'Kaggle_HeartAttack_Prediction_heart' created successfully!
Table 'Kaggle_HeartAttack_Prediction_o2Saturation' created successfully!
Table 

KeyboardInterrupt: 